Написать программу для построения обратного индекса с учетом морфологического анализа. Необходимо реализовать возможность поиска по нескольким словам.

In [1]:
import os
import pickle
import json
from tqdm import tqdm
import nltk
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer

from collections import defaultdict
from pymystem3 import Mystem


Lemmatizer = Mystem()
Stemmer = SnowballStemmer("russian")


def lemmatize_sentence(text):
    lemmas = Lemmatizer.lemmatize(text)
    return "".join(lemmas).strip()


def tokenize_text(text, lemmatize=False, stem=False):
    if lemmatize:
        text = lemmatize_sentence(text)

    tokens = nltk.word_tokenize(text.lower())
    clean_tokens = [
        word
        for word in tokens
        if word.isalnum() and word not in stopwords.words("russian")
    ]

    if stem:
        clean_tokens = [Stemmer.stem(word) for word in clean_tokens]

    return clean_tokens


def build_inverted_index(texts, lemmatize, stem):
    inverted_index = defaultdict(list)

    for doc_id, text in tqdm(
        enumerate(texts), desc="Building inverted index", total=len(texts)
    ):
        if text is None:
            continue
        tokens = tokenize_text(text, lemmatize, stem)
        for token in set(tokens):
            inverted_index[token].append(doc_id)
    return inverted_index


def load_inverted_index(path, texts, lemmatize=False, stem=False):
    if os.path.exists(path):
        with open(path, "rb") as f:
            return pickle.load(f)
    else:
        result = build_inverted_index(texts, lemmatize, stem)
        with open(path, "wb") as f:
            pickle.dump(result, f)
        return result


def search(query, inverted_index, lemmatize=False, stem=False):
    query_tokens = set(tokenize_text(query, lemmatize, stem))
    search_results = set()

    for token in query_tokens:
        if token in inverted_index:
            if not search_results:
                search_results = set(inverted_index[token])
            else:
                search_results = search_results.intersection(set(inverted_index[token]))

    return search_results

In [2]:
with open("../naked_science_corpus.json", "r") as f:
    data = json.load(f)

texts = [article["text"] for article in data]

inverted_index = load_inverted_index("inverted_index.pickle", texts, lemmatize=True)

In [3]:
query = "искуственный интеллект"
results = search(query, inverted_index)

print('Результаты поиска для запроса "{}":'.format(query))
for result in results:
    print(result, texts[result])

Результаты поиска для запроса "искуственный интеллект":
2050 Новое исследование описывает неизвестные ранее защитные механизмы туберкулезной палочки. Устойчивость микобактерий туберкулеза к антибиотикам и выживание в ловушке макрофагов – клетках иммунной системы – обусловлены многослойной оболочкой из миколовых кислот – длинных цепочек атомов углерода, водорода и кислорода. Когда они сворачиваются в клубок, оболочка становится рыхлой и более проницаемой, чем более они развернуты, тем сильнее бактерия защищена. Особенно плотной клеточная стенка туберкулезной палочки становится в кислой среде. «Описать структуру микобактерий туберкулеза экспериментальными методами не так просто, поэтому теоретические подходы выходят на первый план. Сегодня наши вычислительные мощности – на уровне лучших лабораторий в мире. Они позволили построить модель клеточной стенки, которая насчитывает до 300 тысяч атомов. Мы можем наблюдать поведение бактерии с точностью до 1,5 микросекунд, а молекулярно-динамическ

In [4]:
query = "ядерная физика"
results = search(query, inverted_index)

print('Результаты поиска для запроса "{}":'.format(query))
for result in results:
    print(result, texts[result])

Результаты поиска для запроса "ядерная физика":
2560 Статья «Теоретические аспекты химических мутагенов и фенотипических активаторов роста растений, разработанные И. А. Рапопортом (обзор литературных источников)» биологов Института биохимической физики имени Н. М. Эмануэля Российской академии наук (Москва) Ларисы Вайсфельд и Тюменского государственного университета Нины Боме вышла в журнале «Биосфера». На основе литературных источников в статье изложена краткая история открытия мутагенеза, индуцированного ионизирующей радиацией и химическими веществами. Мутагенное действие рентгеновского излучения было открыто в 1928 году американским ученым Генрихом Меллером. Меллер впервые показал, что воздействие рентгеновских лучей на личинок мух увеличивает в сотни и тысячи раз скорость мутагенеза у взрослых особей — строго пропорционально полученной личинками дозе облучения. В 1946 году после трагедии в Хиросиме и Нагасаки Меллер был номинирован на Нобелевскую премию по физиологии и медицине «за 